In [2]:
import os
import re

import tensorflow as tf
import tensorflow.python.platform
from tensorflow.python.platform import gfile
import numpy as np
import pandas as pd
import sklearn
#from sklearn import cross_validation
from sklearn.metrics import accuracy_score, confusion_matrix
from sklearn.svm import SVC, LinearSVC
import matplotlib.pyplot as plt
%matplotlib inline
import pickle

In [3]:
model_dir = '/home/king/DeepLearning/tensorflow/tensorflow/models/image/imagenet/TUTORIAL_DIR/imagenet'
images_dir = '/media/king/DeepVision/images/'
images_dir = '/media/king/DeepVision/phone_cut_refine/'
key_images = [images_dir+f for f in os.listdir(images_dir) if re.search('jpg|JPG|jpeg|JPEG', f)]

#the feature image is in the list_image


In [4]:
print(key_images)

['/media/king/DeepVision/phone_cut_refine/37.jpeg']


In [5]:
def create_graph(model_path):
    """
    create_graph loads the inception model to memory, should be called before
    calling extract_features.
 
    model_path: path to inception model in protobuf form.
    """
    with gfile.FastGFile(model_path, 'rb') as f:
        graph_def = tf.GraphDef()
        graph_def.ParseFromString(f.read())
        _ = tf.import_graph_def(graph_def, name='')

def extract_features(image_paotths, verbose=False):
    """
    extract_features computed the inception bottleneck feature for a list of images
 
    image_paths: array of image path
    return: 2-d array in the shape of (len(image_paths), 2048)
    """
    feature_dimension = 2048
    features = np.empty((len(image_paths), feature_dimension))
 
    with tf.Session() as sess:
        flattened_tensor = sess.graph.get_tensor_by_name('pool_3:0')
 
        for i, image_path in enumerate(image_paths):
            if verbose:
                print('Processing %s...' % (image_path))
 
            if not gfile.Exists(image_path):
                tf.logging.fatal('File does not exist %s', image)
 
            image_data = gfile.FastGFile(image_path, 'rb').read()
            feature = sess.run(flattened_tensor, {
                'DecodeJpeg/contents:0': image_data
            })
            features[i, :] = np.squeeze(feature)
 
    return features 

In [6]:
def create_graph():
    with gfile.FastGFile(os.path.join( model_dir, 'classify_image_graph_def.pb'), 'rb') as f:
        graph_def = tf.GraphDef()
        graph_def.ParseFromString(f.read())
        _ = tf.import_graph_def(graph_def, name='')
    
def extract_features(list_images):
    nb_features = 2048
    features = np.empty((len(list_images),nb_features))
    labels = []

    create_graph()

    with tf.Session() as sess:

        next_to_last_tensor = sess.graph.get_tensor_by_name('pool_3:0')

        for ind, image in enumerate(list_images):
            #if (ind%1 == 0):
                #print('Processing %s...' % (image))
            if not gfile.Exists(image):
                tf.logging.fatal('File does not exist %s', image)

            image_data = gfile.FastGFile(image, 'rb').read()
            try:
                print(1.1)
                predictions = sess.run(next_to_last_tensor,{'DecodeJpeg/contents:0': image_data})
                print(1.2)
                features[ind,:] = np.squeeze(predictions)
                labels.append(re.split('_\d+',image.split('/')[5])[0])
            except:
                continue

    return features, labels

In [ ]:
features,labels = extract_features(key_images)
print(labels)

1.1


In [7]:
pickle.dump(features, open('features', 'wb'))
pickle.dump(labels, open('labels', 'wb'))


In [4]:

features = pickle.load(open('features'))
labels = pickle.load(open('labels'))

print features
print labels

[[0.18121682 0.16582555 0.5762257  ... 0.18307437 0.20829731 0.00314373]
 [0.25238484 0.28684524 0.16730319 ... 0.24109213 0.6040349  0.14139585]
 [0.76935565 0.50966454 0.5571636  ... 0.12974873 0.467812   0.13590123]
 ...
 [0.19292536 0.11586335 0.17199573 ... 0.         0.79579103 0.04432206]
 [0.51969069 0.39638883 0.28552806 ... 0.00827998 0.39981791 0.34388205]
 [0.28053823 0.09174922 0.54782671 ... 0.27112901 0.40139297 0.05562004]]
['6804209.jpeg', '27256471905.jpeg', '28654167732.jpeg', '27684035980.jpeg', '12736908804.jpeg', '19743110647.jpeg', '25604526282.jpeg', '7432803.jpeg', '28628010649.jpeg', '6674951.jpeg', '6914925.jpeg', '7233933.jpeg', '27450197108.jpeg', '27169498351.jpeg', '28446494095.jpeg', '7135710.jpeg', '28672780058.jpeg', '27306789950.jpeg', '28283930536.jpeg', '14904849950.jpeg', '27685524602.jpeg', '26940026078.jpeg', '28751719482.jpeg', '27685916020.jpeg', '26673828810.jpeg', '26146231236.jpeg', '13852810192.jpeg', '27328606756.jpeg', '26630144236.jpeg',

In [5]:
X_train, X_test, y_train, y_test = cross_validation.train_test_split(features, labels, test_size=0.0, random_state=42)

In [6]:
clf = LinearSVC(C=1.0, loss='squared_hinge', penalty='l2',multi_class='ovr')
clf.fit(X_train, y_train)
#y_pred = clf.predict(X_test)
#9.6

LinearSVC(C=1.0, class_weight=None, dual=True, fit_intercept=True,
     intercept_scaling=1, loss='squared_hinge', max_iter=1000,
     multi_class='ovr', penalty='l2', random_state=None, tol=0.0001,
     verbose=0)

In [ ]:
from sklearn.multiclass import OneVsRestClassifier
clf = OneVsRestClassifier(SVC(kernel='linear', probability=True, class_weight='balanced'), n_jobs=-1)
clf.fit(X_train, y_train)

In [ ]:
print X_train
print y_train
pickle.dump(clf, open('clf', 'wb'))

In [12]:
clf = pickle.load(open('clf'))

In [17]:
#all the JD images
JD_images_dir = '/home/king/JDimage/'
JD_list_images = [JD_images_dir+f for f in os.listdir(JD_images_dir) if re.search('jpg|JPG|jpeg|JPEG', f)]
JD_features,JD_labels = extract_features(JD_list_images)
#how big the features and labels can be

Processing JDimage/1736742637.jpeg...
Processing JDimage/11492326213.jpeg...
Processing JDimage/11498545616.jpeg...
Processing JDimage/10782385276.jpeg...
Processing JDimage/10938079452.jpeg...
Processing JDimage/11252368724.jpeg...
Processing JDimage/10128713153.jpeg...
Processing JDimage/1643572925.jpeg...
Processing JDimage/11286525787.jpeg...
Processing JDimage/11247139684.jpeg...
Processing JDimage/10850537838.jpeg...
Processing JDimage/2536942.jpeg...
Processing JDimage/11403765874.jpeg...
Processing JDimage/10376619777.jpeg...
Processing JDimage/11282351602.jpeg...
Processing JDimage/10728874600.jpeg...
Processing JDimage/11454484604.jpeg...
Processing JDimage/2649433.jpeg...
Processing JDimage/10926714585.jpeg...
Processing JDimage/11010953083.jpeg...
Processing JDimage/10914042359.jpeg...
Processing JDimage/1789124252.jpeg...
Processing JDimage/11618665769.jpeg...
Processing JDimage/10866863024.jpeg...
Processing JDimage/10711231047.jpeg...
Processing JDimage/10745344345.jpeg.

In [18]:
y_pred = clf.predict(JD_features)
print len(JD_labels)
print len(y_pred)

3565
3565


In [19]:
for dirName in y_train:
    os.makedirs("/media/king/DeepVision/JDimage_result_1/"+dirName)

In [20]:
import shutil

In [21]:
for dirName in y_train:
    #os.makedirs("/media/king/DeepVision/JDimage_result/"+dirName)
    shutil.copy2('/media/king/DeepVision/JDimage/'+dirName,"/media/king/DeepVision/JDimage_result_1/"+dirName)

In [22]:
for JD_image, result in zip(JD_labels, y_pred):
     shutil.copy2('/media/king/DeepVision/JDimage/'+JD_image,"/media/king/DeepVision/JDimage_result_1/"+result)
#the results are putted in the folders

In [3]:
def create_graph():
    with gfile.FastGFile(os.path.join( model_dir, 'classify_image_graph_def.pb'), 'rb') as f:
        graph_def = tf.GraphDef()
        graph_def.ParseFromString(f.read())
        _ = tf.import_graph_def(graph_def, name='')
    
def extract_features(list_images):
    nb_features = 2048
    features = np.empty((len(list_images),nb_features))
    labels = []

    create_graph()

    with tf.Session() as sess:

        next_to_last_tensor = sess.graph.get_tensor_by_name('pool_3:0')

        for ind, image in enumerate(list_images):
            #if (ind%1 == 0):
                #print('Processing %s...' % (image))
            if not gfile.Exists(image):
                tf.logging.fatal('File does not exist %s', image)

            image_data = gfile.FastGFile(image, 'rb').read()
            try:
                predictions = sess.run(next_to_last_tensor,{'DecodeJpeg/contents:0': image_data})
                features[ind,:] = np.squeeze(predictions)
                labels.append(re.split('_\d+',image.split('/')[5])[0])
            except:
                continue

    return features, labels

In [4]:
images_dir = '/media/king/DeepVision/images_bigger/'
key_images = [images_dir+f for f in os.listdir(images_dir) if re.search('jpg|JPG|jpeg|JPEG', f)]
key_images='/media/king/DeepVision/images/10035977224.jpeg'
print(re.split('_\d+',key_images.split('/')[5])[0])

10035977224.jpeg


In [5]:
images_dir = '/media/king/DeepVision/images_bigger/'
key_images = [images_dir+f for f in os.listdir(images_dir) if re.search('jpg|JPG|jpeg|JPEG', f)]
features_big,labels_big = extract_features(key_images)
print(labels_big)

['10000149447 (3rd copy).jpeg', '10000149447 (another copy).jpeg', '10000149447 (copy).jpeg', '10000149447.jpeg', '10000166138 (3rd copy).jpeg', '10000166138 (another copy).jpeg', '10000166138 (copy).jpeg', '10000166138.jpeg', '10001592870 (3rd copy).jpeg', '10001592870 (another copy).jpeg', '10001592870 (copy).jpeg', '10001592870.jpeg', '10008870322 (3rd copy).jpeg', '10008870322 (another copy).jpeg', '10008870322 (copy).jpeg', '10008870322.jpeg', '10013888749 (3rd copy).jpeg', '10013888749 (another copy).jpeg', '10013888749 (copy).jpeg', '10013888749.jpeg', '10014108225 (3rd copy).jpeg', '10014108225 (another copy).jpeg', '10014108225 (copy).jpeg', '10014108225.jpeg', '10015399245 (3rd copy).jpeg', '10015399245 (another copy).jpeg', '26998173782 (3rd copy).jpeg', '26998173782 (another copy).jpeg', '26998173782 (copy).jpeg', '26998173782.jpeg', '26998176046 (3rd copy).jpeg', '26998176046 (another copy).jpeg', '26998176046 (copy).jpeg', '26998176046.jpeg', '26998176606 (3rd copy).jpeg'

In [6]:
#print(features_big.size)
print(len(features_big))
print(len(labels_big))
#print(labels_big)

214514
214513


In [7]:
from sklearn.externals import joblib
filename = 'features_big.sav'
joblib.dump(features_big, filename)
filename2 = 'labels_big.sav'
joblib.dump(labels_big, filename2)

['labels_big.sav']

In [ ]:
features_big = pickle.load(open('features_big'))
labels_big = pickle.load(open('labels_big'))

print features_big
print labels_big

In [3]:
from sklearn.externals import joblib
features_big = joblib.load('features_big.sav')
labels_big = joblib.load('labels_big.sav')

In [4]:
X_train, X_test, y_train, y_test = cross_validation.train_test_split(features_big[0:214513], labels_big, test_size=0.0, random_state=42)

In [ ]:
clf = LinearSVC(C=1.0, loss='squared_hinge', penalty='l2',multi_class='ovr')
clf.fit(X_train, y_train)
#y_pred = clf.predict(X_test)
#9.6

In [ ]:
y_pred = clf.predict(features_big[100])
print(y_pred)

In [ ]:
from sklearn.externals import joblib
filename = 'finalized_clf_100k.sav'
joblib.dump(clf, filename)

In [ ]:
loaded_model = joblib.load(filename)

In [ ]:
y_pred = loaded_model.predict(features_big[100])
print(y_pred)